In [72]:
import pandas as pd
import urllib
import requests
import nltk
from nltk.corpus import stopwords
import spacy
from more_itertools import unique_everseen
import os
import re

nlp = spacy.load('en')
nltk.download('all')

[nltk_data] Downloading collection 'all'
[nltk_data]    | 
[nltk_data]    | Downloading package abc to /Users/laus03/nltk_data...
[nltk_data]    |   Package abc is already up-to-date!
[nltk_data]    | Downloading package alpino to
[nltk_data]    |     /Users/laus03/nltk_data...
[nltk_data]    |   Package alpino is already up-to-date!
[nltk_data]    | Downloading package biocreative_ppi to
[nltk_data]    |     /Users/laus03/nltk_data...
[nltk_data]    |   Package biocreative_ppi is already up-to-date!
[nltk_data]    | Downloading package brown to
[nltk_data]    |     /Users/laus03/nltk_data...
[nltk_data]    |   Package brown is already up-to-date!
[nltk_data]    | Downloading package brown_tei to
[nltk_data]    |     /Users/laus03/nltk_data...
[nltk_data]    |   Package brown_tei is already up-to-date!
[nltk_data]    | Downloading package cess_cat to
[nltk_data]    |     /Users/laus03/nltk_data...
[nltk_data]    |   Package cess_cat is already up-to-date!
[nltk_data]    | Downloading p

True

In [5]:
df_fake = pd.read_csv('/Users/laus03/Documents/bbc_projects/fake_news/fake_news_video/fake-video-corpus - fake-videos.tsv', sep='\t')
df_real = pd.read_csv('/Users/laus03/Documents/bbc_projects/fake_news/fake_news_video/fake-video-corpus - real-videos.tsv', sep='\t')

In [121]:
def getEntities(sentence):
    #lower case
    sentence = sentence.lower()
    sentence_clean = re.sub('[!@#$\/":().|,]', ' ', sentence)
    # tokenise sentence
    tokens = nltk.word_tokenize(sentence_clean)
    # filtering out stop words
    filtered_words = [word for word in tokens if word not in stopwords.words('english')]
    # entity extraction
    entities = nltk.pos_tag(filtered_words)

    list_tags_keep = ['NN', 'NNS', 'NNP', 'NNPS', 'VB','VBD', 'VBG', 'VBN', 'VBP', 'VBZ']
    entities_1 = [w[0] for w in entities if w[1] in list_tags_keep]
    entities_final = list(unique_everseen(entities_1))
    
    return entities_final

In [122]:
articles = []
article_content = os.listdir("/Users/laus03/Documents/bbc_projects/fake_news/Results")
for x in article_content:
    with open('/Users/laus03/Documents/bbc_projects/fake_news/Results/{}'.format(x),encoding='utf-8', errors='ignore') as f:
        data = f.read().replace('\n', '')
        articles.append(data)

In [130]:
test = [*map(getEntities, articles)]

In [132]:
test[0]

['men',
 'language',
 'competition200',
 'people',
 'participatingchallenge',
 'peacefulness',
 'happinessand',
 'calmness',
 'sentence',
 'person',
 'wrote',
 'wife',
 'sleeping',
 'received',
 'standing',
 'ovation',
 'form',
 'judgesand',
 'audience',
 'married',
 'judge',
 'stage',
 'hugged',
 'tears',
 'eyes',
 'andsaid',
 'dt',
 '%']

In [154]:
news_twitter = pd.read_csv('fake_news_twitter.csv', encoding='ISO-8859-1')

In [156]:
news_twitter['entities'] = news_twitter['text'].apply(lambda x: getEntities(x))

In [162]:
news_twitter['text'][0]

'RT @Swamy39: Why the likes of Chidambaram, Karti, go Scot-free despite charges against them https://t.co/bg0g1HiMLQ via @PGurus1'

In [161]:
news_twitter['entities'][0]

['rt',
 'swamy39',
 'likes',
 'chidambaram',
 'karti',
 'go',
 'charges',
 'https',
 'bg0g1himlq',
 'pgurus1']

In [58]:
sentence = 'young girl shireya bombed while singing - Syria'
getEntities(sentence)

['girl', 'shireya', 'bombed', 'singing', 'syria']

In [52]:
sentence = "Dhruv verma is missing, 14yrs My friends son Dhruv Verma is missing from yesterday 7am from Airoli St Xavier School. Last location kopar kahiarane sec - 2 Kindly circulate his pics as much as you can to all your contacts. If recevied any hint pls call +917506943822"
getEntities(sentence)

['verma',
 'missing',
 'yesterday',
 'location',
 'kopar',
 'kahiarane',
 'sec',
 'hint',
 'pls',
 'call',
 '+917506943822']

## Twitter api

In [137]:
#Import the necessary methods from tweepy library
import pandas as pd
from tweepy.streaming import StreamListener
from tweepy import OAuthHandler
from tweepy import Stream
from textblob import TextBlob
from sqlalchemy import create_engine
from sqlalchemy.exc import ProgrammingError
import json
import dataset
import datetime

In [138]:
# authentication keys & tokens
access_token = "3032303812-l2m1iFqL175WupWs5Sv5DaD4apLkTeJTvxLa5wc"
access_token_secret = "DNnElLtEAmlpzIdC8Hbu9knRZbhlDaC5kkTAEcby440tA"
consumer_key = "bdkjT6DLAfrXZh0QxivaU4wHU"
consumer_secret = "jyFGmiZ0Nu85teeCyY9Dw6mzfYtwfgjq6izolAZTntIGXs9GYX"


In [163]:
class Listener(StreamListener):

    def on_status(self, status):
        # if retweeted_status property exists then don't process tweet
        #if status.retweeted:
        #    return

        # fields of interest
        description = status.user.description
        loc = status.user.location
        text = status.text
        coords = status.coordinates
        geo = status.geo
        name = status.user.screen_name
        user_created = status.user.created_at
        followers = status.user.followers_count
        id_str = status.id_str
        created = status.created_at
        retweets = status.retweet_count
        
        # stored as dictionary but json.dump returns as string so we can write to db table
        if geo is not None:
            geo = json.dumps(geo)

        if coords is not None:
            coords = json.dumps(coords)
            
        try:
            # writing data to postgres
            df_tweets = pd.DataFrame({'user_description':[], 'user_location':[], 'coordinates':[], 'text':[],
                                     'geo':[], 'user_name':[], 'user_created':[], 'user_followers':[], 'id_str':[],
                                     'created':[], 'retweet_count':[]})
            df_tweets = df_tweets.append({'user_description': description, 
                                          'user_location': loc, 
                                          'coordinates': coords, 
                                          'text': text,
                                          'geo': geo, 
                                          'user_name': name, 
                                          'user_created': user_created, 
                                          'user_followers': followers, 
                                          'id_str': id_str,
                                          'created':created, 
                                          'retweet_count':retweets}, ignore_index=True) 
            #engine = create_engine(engine_string)
            #df_tweets.to_sql('election_tweets', engine, index = False, if_exists = 'append')
            with open('fake_news_twitter.csv', 'a') as f:
                df_tweets.to_csv(f, header=False, index=False)
        except ProgrammingError as err:
            print(err)

        
        print(status)

    def on_error(self, status_code):
        print(status_code)
        if status_code == 420:
            #returning False in on_data disconnects the stream
            return False

In [ ]:
# 2.Using that class create a Stream object (initialising class created above)
#This handles Twitter authetification and the connection to Twitter Streaming API
auth = OAuthHandler(consumer_key, consumer_secret)
auth.set_access_token(access_token, access_token_secret)
twitterStream = Stream(auth, Listener())

# 3.Connect to the Twitter API using the Stream.
twitterStream.filter(track=['@tadkanews', '@saveratimes', '@Live_Hindustan', '@hindutvamedia', '@SangbadPratidin',
                            '@SatyaVijayi', '@udayavani_web', '@Opindia_com', '@rightlog_in', '@NewsroomPostCom', '@liveindia3',
                            '@logicalbharat', '@firkee_in', '@theRajivDixit', '@HawkFeed', '@srishtanews',
                            '@TIP_Pradhanjii', '@pGurus1', '@IndiaFactsOrg', '@agniveer', '@repitition', '@upananda',
                            '@TFearlessIndian', '@hindupost', '@guruprasad_gp', '@myind.net', '@ShankhNaad', '@The_Dailygraph_',
                            '@janman_tv', '@jankrantinews', '@internetHINDU13', '@TheSanatanTimes', '@jagritbharat',
                            '@NavbharatTimes', '@acrossUpdate', '@lnnindia', '@ExcuseMedia', 'humlogFB'])

Status(_api=<tweepy.api.API object at 0x10c0e2d30>, _json={'created_at': 'Thu Nov 15 04:19:34 +0000 2018', 'id': 1062923036704292864, 'id_str': '1062923036704292864', 'text': 'RT @achlendra: चंडीगढ़: भाजपा विधायक दल की बैठक ख़त्म, प्रधानमंत्री @narendramodi की गुरुग्राम रैली से पहले हुआ मंथन, मुख्यमंत्री मनोहर लाल…', 'source': '<a href="http://twitter.com/download/android" rel="nofollow">Twitter for Android</a>', 'truncated': False, 'in_reply_to_status_id': None, 'in_reply_to_status_id_str': None, 'in_reply_to_user_id': None, 'in_reply_to_user_id_str': None, 'in_reply_to_screen_name': None, 'user': {'id': 2838845809, 'id_str': '2838845809', 'name': 'Harendra Singh ⚓', 'screen_name': 'NavalVeteran_HB', 'location': 'Gurgaon', 'url': None, 'description': '🇮🇳⚔️ Veteran and Nationalist🇮🇳⚔️', 'translator_type': 'none', 'protected': False, 'verified': False, 'followers_count': 52, 'friends_count': 84, 'listed_count': 1, 'favourites_count': 604, 'statuses_count': 3065, 'created_at': 'Fri Oct 0

Status(_api=<tweepy.api.API object at 0x10c0e2d30>, _json={'created_at': 'Thu Nov 15 04:19:38 +0000 2018', 'id': 1062923053212958720, 'id_str': '1062923053212958720', 'text': 'RT @Rishabh25888: @RenukaJain6 @TrulyMonica @AsYouNotWish @RituRathaur @Kuvalayamala @anjanaomkashyap @nishantchat @amitmalviya @AskAnshul…', 'source': '<a href="http://twitter.com/download/android" rel="nofollow">Twitter for Android</a>', 'truncated': False, 'in_reply_to_status_id': None, 'in_reply_to_status_id_str': None, 'in_reply_to_user_id': None, 'in_reply_to_user_id_str': None, 'in_reply_to_screen_name': None, 'user': {'id': 356861827, 'id_str': '356861827', 'name': '#AshishSaxena 🚩🇮🇳', 'screen_name': 'saxenaa14', 'location': 'भारतवर्ष🚩', 'url': None, 'description': 'Nationalist,Software Engineer,Interested in Politics,Cricket and Technology,views are strictly personal.Retweets ≠ Endorsement.', 'translator_type': 'none', 'protected': False, 'verified': False, 'followers_count': 605, 'friends_count': 1560, 

Status(_api=<tweepy.api.API object at 0x10c0e2d30>, _json={'created_at': 'Thu Nov 15 04:19:44 +0000 2018', 'id': 1062923078026485760, 'id_str': '1062923078026485760', 'text': 'RT @Swamy39: @4Species @pGurus1 Why did you not change key bureaucrats and law officers after May 26, 2014? Because of the tyranny of the U…', 'source': '<a href="http://twitter.com/download/android" rel="nofollow">Twitter for Android</a>', 'truncated': False, 'in_reply_to_status_id': None, 'in_reply_to_status_id_str': None, 'in_reply_to_user_id': None, 'in_reply_to_user_id_str': None, 'in_reply_to_screen_name': None, 'user': {'id': 1046070219788103680, 'id_str': '1046070219788103680', 'name': 'समविद', 'screen_name': 'SAMVID_001', 'location': 'भारत', 'url': None, 'description': 'भारतीय', 'translator_type': 'none', 'protected': False, 'verified': False, 'followers_count': 2, 'friends_count': 60, 'listed_count': 0, 'favourites_count': 67, 'statuses_count': 57, 'created_at': 'Sat Sep 29 16:12:30 +0000 2018', 'utc_of

Status(_api=<tweepy.api.API object at 0x10c0e2d30>, _json={'created_at': 'Thu Nov 15 04:19:51 +0000 2018', 'id': 1062923105650307072, 'id_str': '1062923105650307072', 'text': '@DrShobha @IndiaFactsOrg Seeking money for poors abroad and glorifying idealogue from that money at home', 'display_text_range': [25, 104], 'source': '<a href="https://mobile.twitter.com" rel="nofollow">Twitter Lite</a>', 'truncated': False, 'in_reply_to_status_id': 1062910694041968641, 'in_reply_to_status_id_str': '1062910694041968641', 'in_reply_to_user_id': 99034397, 'in_reply_to_user_id_str': '99034397', 'in_reply_to_screen_name': 'DrShobha', 'user': {'id': 158606166, 'id_str': '158606166', 'name': 'mohammad allam', 'screen_name': 'allam_allam', 'location': 'Aligarh', 'url': None, 'description': 'Teacher@AMU#Writer#Author#Historian#Educationist & Researcher # Love to work 4 the Humanity#Hate corruption & Terrorism#Love to seek justice 4 everyone.', 'translator_type': 'none', 'protected': False, 'verified': Fa

Status(_api=<tweepy.api.API object at 0x10c0e2d30>, _json={'created_at': 'Thu Nov 15 04:19:56 +0000 2018', 'id': 1062923127267696640, 'id_str': '1062923127267696640', 'text': 'RT @DrShobha: Towering resentment: Why the British are sulking over the Statue of Unity | IndiaFacts https://t.co/bu7HCaTZuJ via @IndiaFact…', 'source': '<a href="http://twitter.com/download/android" rel="nofollow">Twitter for Android</a>', 'truncated': False, 'in_reply_to_status_id': None, 'in_reply_to_status_id_str': None, 'in_reply_to_user_id': None, 'in_reply_to_user_id_str': None, 'in_reply_to_screen_name': None, 'user': {'id': 92548871, 'id_str': '92548871', 'name': 'Swamiye Sharanam Ayyappa', 'screen_name': 'MorbidMortal', 'location': 'Hyderabad', 'url': 'http://angelsenvydevilspride.blogspot.com/', 'description': 'Maverick AP07-OD10-AP31-AP28-TN02-AP28-RJ14-KA03-AP28-RJ14-CG04-OD02-HR26-AP28 Living:TS07 Nativity ❎Sure;Right Thinking;Religious ❎Spiritual;RTs ❎endorsments', 'translator_type': 'none', 'prote

...

Status(_api=<tweepy.api.API object at 0x10c0e2d30>, _json={'created_at': 'Thu Nov 15 04:45:31 +0000 2018', 'id': 1062929566681812993, 'id_str': '1062929566681812993', 'text': 'RT @Swamy39: Why the likes of Chidambaram, Karti, go Scot-free despite charges against them https://t.co/bg0g1HiMLQ via @PGurus1', 'source': '<a href="http://twitter.com/download/android" rel="nofollow">Twitter for Android</a>', 'truncated': False, 'in_reply_to_status_id': None, 'in_reply_to_status_id_str': None, 'in_reply_to_user_id': None, 'in_reply_to_user_id_str': None, 'in_reply_to_screen_name': None, 'user': {'id': 964530053597028354, 'id_str': '964530053597028354', 'name': 'Narpatsinh Chudasama', 'screen_name': 'narpatsinhgmai1', 'location': 'Gandhidham, India', 'url': None, 'description': 'Worked as GM, Commercial. Environment friendly, interested in History, Geography, Politics, Music and reading spiritual.', 'translator_type': 'none', 'protected': False, 'verified': False, 'followers_count': 36, 'friend

Status(_api=<tweepy.api.API object at 0x10c0e2d30>, _json={'created_at': 'Thu Nov 15 04:45:32 +0000 2018', 'id': 1062929571471736832, 'id_str': '1062929571471736832', 'text': 'RT @Etahpolice: #PaperCuttingUpp #UPPolice \nएसएसपी एटा द्वारा जनपद में शुरू किए गया #NewInitiativeUpp, "पुलिस ट्रेनिंग एप" के माध्यम से रि…', 'source': '<a href="http://twitter.com/download/android" rel="nofollow">Twitter for Android</a>', 'truncated': False, 'in_reply_to_status_id': None, 'in_reply_to_status_id_str': None, 'in_reply_to_user_id': None, 'in_reply_to_user_id_str': None, 'in_reply_to_screen_name': None, 'user': {'id': 927615872822272000, 'id_str': '927615872822272000', 'name': '@pankaj', 'screen_name': 'Nsoy2mtSngLK24D', 'location': 'Uttar Pradesh, India', 'url': None, 'description': '0000', 'translator_type': 'none', 'protected': False, 'verified': False, 'followers_count': 100, 'friends_count': 170, 'listed_count': 0, 'favourites_count': 260, 'statuses_count': 267, 'created_at': 'Mon Nov 06 19:17

Status(_api=<tweepy.api.API object at 0x10c0e2d30>, _json={'created_at': 'Thu Nov 15 04:45:37 +0000 2018', 'id': 1062929591973556224, 'id_str': '1062929591973556224', 'text': 'बैंकों के राष्ट्रीयकरण से जनता का फायदा नहीं हुआ बल्कि मोदी के सामान्य करण से हुआ है : राजनाथ सिंह #bjp… https://t.co/XMcg1TeLUl', 'source': '<a href="http://twitter.com/download/android" rel="nofollow">Twitter for Android</a>', 'truncated': True, 'in_reply_to_status_id': None, 'in_reply_to_status_id_str': None, 'in_reply_to_user_id': None, 'in_reply_to_user_id_str': None, 'in_reply_to_screen_name': None, 'user': {'id': 1288766066, 'id_str': '1288766066', 'name': 'Gulshan Rai Khatri', 'screen_name': 'gulshanNBT', 'location': 'New Delhi', 'url': 'http://navbharattimes.indiatimes.com/', 'description': 'Special correspondent, Navbharat Times, Reports on Politics, also on Aviation, Railway, metro, and Road Transport.  views are personal.', 'translator_type': 'none', 'protected': False, 'verified': False, 'followers_c

Status(_api=<tweepy.api.API object at 0x10c0e2d30>, _json={'created_at': 'Thu Nov 15 04:45:47 +0000 2018', 'id': 1062929632528261120, 'id_str': '1062929632528261120', 'text': '@agniveer जय सनातन धर्म की 🚩🙏', 'display_text_range': [10, 29], 'source': '<a href="https://mobile.twitter.com" rel="nofollow">Twitter Lite</a>', 'truncated': False, 'in_reply_to_status_id': 1062925756467236864, 'in_reply_to_status_id_str': '1062925756467236864', 'in_reply_to_user_id': 57141786, 'in_reply_to_user_id_str': '57141786', 'in_reply_to_screen_name': 'agniveer', 'user': {'id': 2530271066, 'id_str': '2530271066', 'name': 'धीरेंद्र राष्ट्रवादी', 'screen_name': 'smart_tiwari', 'location': 'Bidhuna indai', 'url': None, 'description': 'राष्ट्र और धर्म पहले ।\nॐ *सनातनी हिन्दू * ॐ', 'translator_type': 'none', 'protected': False, 'verified': False, 'followers_count': 84, 'friends_count': 96, 'listed_count': 0, 'favourites_count': 8928, 'statuses_count': 6813, 'created_at': 'Wed May 28 15:35:10 +0000 2014', 'ut

Status(_api=<tweepy.api.API object at 0x10c0e2d30>, _json={'created_at': 'Thu Nov 15 04:45:49 +0000 2018', 'id': 1062929641394958337, 'id_str': '1062929641394958337', 'text': 'RT @trramesh: Is the Commie CM planning the next TDB with one Commie "Hindu" member, one Muslim member and one Bishop like Franco? Sabarima…', 'source': '<a href="http://twitter.com/download/android" rel="nofollow">Twitter for Android</a>', 'truncated': False, 'in_reply_to_status_id': None, 'in_reply_to_status_id_str': None, 'in_reply_to_user_id': None, 'in_reply_to_user_id_str': None, 'in_reply_to_screen_name': None, 'user': {'id': 957570439374553088, 'id_str': '957570439374553088', 'name': 'Gagan K', 'screen_name': 'AhinsakC', 'location': 'Gujarat, India', 'url': None, 'description': "Love My Motherland- Bharat, Engineer by profession| Bhartiya by Religion| Devotee to Hindu Sunskriti & it's pious Saints", 'translator_type': 'none', 'protected': False, 'verified': False, 'followers_count': 55, 'friends_count': 2